In [1]:
from neuron import h, gui
import bokeh as bk
import bokeh.plotting as bkp
import numpy as np
from bokeh.palettes import Dark2_5 as palette
import itertools 
import ipywidgets as widgets
from branched_cable import branched_cable, run_current_clamp, run_sim

from matplotlib import pyplot as plt
%matplotlib inline

colors = itertools.cycle(palette)  
bkp.output_notebook()

%load_ext autoreload
%autoreload 2

celsius = 34.0  

Loading BokehJS ...

Add spine and now put synapse onto spine

In [30]:
# ball and stick 

##### edit these variables to change cable properties
soma_diam = 12
soma_L=12
dend_diam=1
dend_L=250
dend_Ra=180
Rm=2800
stim_loc=1
tstop = 200
########

def ball_stick_spine(spine_loc=.67,isyn_loc = .5, isyn_delay=.1,
                    gkdrbar_soma=.01,gnabar_soma=.01,gkinbar_soma=.008,ghbar_soma=.0001,
                    gkdrbar_dend=0,gnabar_dend=0,gkinbar_dend=0,ghbar_dend=0,
                    spine_tau=1,spine_num=1,spine_e=0,spine_weight=.05,
                    inh_tau=1,inh_num=1,inh_e=-80,inh_weight=.05,
                    soma_noise_gain=.09, dend_noise_gain=.09,
                    neck_resistance=500,basal_dends = False):
    
    # build cell with 1 branch and 1 spine
    cell = branched_cable()
    cell.make_cable(soma_diam,soma_L,Rm=Rm,Vrest=-55)
    # branch
    cell.add_branch('cable',1,dend_L,dend_diam,Ra=dend_Ra,Rm=Rm,Vrest=-55) 
    #spine
    cell.add_branch('branch',spine_loc,.01,.01,Ra=neck_resistance,Rm=Rm,segname='spine',nseg=1) 
    
    # add 2 basal dendrites if requested
    if basal_dends:
        cell.add_branch('cable',0,dend_L/5,dend_diam/2,
                        Ra=dend_Ra,Rm=Rm,Vrest=-55,segname='basal0')
        cell.add_branch('cable',0,dend_L/5,dend_diam/2,
                       Ra = dend_Ra,Rm=Rm,Vrest=-55,segname='basal1')

    # add channels to soma and branch
    cell.channel_control('cable',kdr=True,gkdrbar=gkdrbar_soma,
                         na=True,gnabar=gnabar_soma,
                         kin=True,gkinbar=gkinbar_soma,
                         h=True,ghbar=ghbar_soma)
    cell.channel_control('branch',kdr=True,gkdrbar=gkdrbar_dend,
                         na=True, gnabar=gnabar_dend,
                         kin=True, gkinbar=gkinbar_dend,
                         h=True,ghbar=ghbar_dend)

    #add recording vectors
    figs = []
    if basal_dends:
        num_rec_vecs = 8
        cell.recording_vecs([['cable',.5,'v'],['branch',.25,'v'],
                        ['branch',.5,'v'],['branch',.75,'v'],
                         ['spine',1,'v'],['branch',spine_loc,'v'],
                         ['basal0',.5,'v'],['basal1',.5,'v']])
        
        
    else: 
        num_rec_vecs=6
        cell.recording_vecs([['cable',.5,'v'],['branch',.25,'v'],
                        ['branch',.5,'v'],['branch',.75,'v'],
                         ['spine',1,'v'],['branch',spine_loc,'v']])
    
    figs=[]
    for title in cell.record_vecs:
        if title is not 'time':
            figs.append(bkp.figure(plot_height=200,plot_width=200,title=title))
    
    for i, color in zip(range(3),colors):
        for t in list(np.linspace(2,250,num=2500)):
            if i==0:
                cell.add_IClamp('cable',.5,soma_noise_gain*np.random.uniform(),.1,
                                delay=t,stimname=str(t))
                cell.add_IClamp('branch',.5,dend_noise_gain*np.random.uniform(),.1,
                                delay=t,stimname="branch"+str(t))
            else:
                cell.stims[str(t)].amp = soma_noise_gain*np.random.uniform()
                cell.stims["branch"+str(t)].amp = dend_noise_gain*np.random.uniform()

        if i ==0:    
            #excitatory synapse
            stim = h.NetStim() # Make a new stimulator
            syn_ = h.ExpSyn(cell.segments['spine'](1))
            syn_.e = spine_e
            syn_.tau = spine_tau
            stim.number = spine_num
            stim.interval=.1
            stim.start = 80
            ncstim = h.NetCon(stim, syn_)
            ncstim.delay = 1
            ncstim.weight[0] = spine_weight # NetCon weight is a vector.
            cell.stims['expsyn']=ncstim

            
            # inhibitory synapse
            istim = h.NetStim()
            isyn_ = h.ExpSyn(cell.segments['branch'](.4))
            isyn_.e = inh_e
            isyn_.tau = inh_tau
            istim.number = inh_num
            istim.interval=.1
            istim.start = 80+isyn_delay
            incstim = h.NetCon(istim, isyn_)
            incstim.delay = 1
            incstim.weight[0] = inh_weight# NetCon weight is a vector.
            cell.stims['isyn']=incstim



        t,results = run_sim(cell,tstop = 250)
        #figs=[]
        for i,key in enumerate(results.keys()):
            if key is not 'time':
                vArr =  results[key]
                figs[i-1].line(t[t>50],vArr[t>50],color=color)
            #figs[i].title=key

    if basal_dends:
        layout = bk.layouts.layout([[figs[0],figs[1],figs[2]],
                                    [figs[3],figs[4],figs[5]],
                                    [figs[6],figs[7]]])
    else:
        layout = bk.layouts.layout([[figs[0],figs[1],figs[2]],
                                    [figs[3],figs[4],figs[5]]])
            
    bkp.show(layout)
    return cell, results

# add plots for different compartments
# change spine location
# change inhibitory location
    # change time relative to excitatory synapse




In [32]:
cell,results=ball_stick_spine(spine_loc=.67,isyn_loc = .5, isyn_delay=.1,
                    gkdrbar_soma=.01,gnabar_soma=.01,gkinbar_soma=.008,ghbar_soma=.0001,
                    gkdrbar_dend=0,gnabar_dend=0,gkinbar_dend=0,ghbar_dend=0,
                    spine_tau=1,spine_num=10,spine_e=0,spine_weight=.08,
                    inh_tau=1,inh_num=1,inh_e=-80,inh_weight=.0,
                    soma_noise_gain=.08, dend_noise_gain=.08,
                    neck_resistance=500,basal_dends = True)